In [8]:
from sim import NBodySimulation, generate_disk_galaxy, generateDisk3D, generateDisk3Dv2, generateDisk3Dv3, generateDisk3Dv4
import numpy as np
import torch
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from IPython.display import HTML
import matplotlib.animation as animation
from datagen import *
from Transformer import ContConvTransformer

In [2]:
data = generate_dataset_transformer(1)

Generating dataset with 1 scenes...


100%|██████████| 1/1 [00:14<00:00, 14.35s/it]


In [3]:
data[0]['inputs'].shape

(5, 502, 7)

In [4]:
model = ContConvTransformer(input_dim=7,
                            hidden_dim=32,
                            output_dim=3,
                            num_heads=4)

In [11]:
import time
start = time.time()
for i in range(1000):
    model(torch.tensor(data[0]['inputs']).float())

print(time.time() - start, 's')

8.390767812728882 s


In [6]:
test = [
{'a':np.array([1,2,3]), 'b':np.array([4,5,6])},
{'a':np.array([7,8,9]), 'b':np.array([10,11,12])},
{'a':np.array([13,14,15]), 'b':np.array([16,17,18])},
{'a':np.array([19,20,21]), 'b':np.array([22,23,24])}
]

data = np.random.shuffle(test)
print(data)

None


In [3]:
N = 1000
t_end = 10.0
dt = 0.01
softening = 0.1
G = 1.0
distributions = ['plummer', 'hernquist', 'jaffe', 'isothermal', 'uniform']


particles1 = generateDisk3Dv4(
    nbStars=N,
    radius=1.0,
    Mass=2.0,
    bh_Mass_percentage=0.8,
    zOffsetMax=0.1,
    gravityCst=G,
    distribution='hernquist',
    offset=[-1, 0.0, 0.0],
    initial_vel=[0.0, 0.0, 0.0]
)
particles2 = generateDisk3Dv4(
    nbStars=N,
    radius=1.0,
    Mass=3.0,
    bh_Mass_percentage=0.8,
    zOffsetMax=0.1,
    gravityCst=G,
    distribution='hernquist',
    offset=[1, 0.0, 0.0],
    initial_vel=[0.0, 0.0, 0.0]
)



particles = particles1 + particles2



In [4]:
sim = NBodySimulation(particles, G, softening, dt)
pos, vel, acc, KE, PE, _, mass_save = sim.run(t_end, plot_real_time=False, save_states=True)

 33%|███▎      | 330/1000 [01:08<02:19,  4.80it/s]


KeyboardInterrupt: 

In [17]:
def animate3d(pos_save, mass_save=None, bh_num = 2):

    fig = plt.figure(figsize=(8, 8))
    ax = fig.add_subplot(111, projection='3d')
    ax.set_xlim(-2, 2)
    ax.set_ylim(-2, 2)
    ax.set_zlim(-2, 2)
    
    
    
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    ax.set_zlabel('z')


    ax.set_xticks([])
    ax.set_yticks([])
    ax.set_zticks([])




    # get index of 2 biggest masses
    bh_index = np.argsort(mass_save)[::-1][:bh_num]

    masses_without_bh = np.delete(mass_save, bh_index)

    max_mass = np.max(masses_without_bh)
    min_mass = np.min(masses_without_bh)

    
    # Create the colormap (inferno)
    cmap = plt.cm.autumn
    colors = np.zeros((pos_save.shape[0], 4))


    for i in range(pos_save.shape[0]):
        if i in bh_index:
            colors[i] = [0, 0, 0, 1]
        else:
            colors[i] = cmap((mass_save[i] - min_mass) / (max_mass - min_mass))

    scat = ax.scatter(pos_save[:, 0, 0], pos_save[:, 1, 0], pos_save[:, 2, 0], c=colors)

    def update(i):
        # Update the positions of the particles
        scat._offsets3d = (pos_save[:, 0, i], pos_save[:, 1, i], pos_save[:, 2, i])
        
        # Optionally update sizes if mass_save changes per timestep (if desired)
        if mass_save is not None:
            masses = mass_save[:pos_save.shape[0]]
            masses = 100 * np.sqrt(masses)
            masses[bh_index] = 10
            
            scat.set_sizes(masses)

    ani = animation.FuncAnimation(fig, update, frames=pos_save.shape[2], interval=10)
    plt.close(fig)
    return HTML(ani.to_html5_video())

animate3d(pos, mass_save, bh_num=2)